In [1]:
# import main library
import ee
import geemap
import osi
import pandas as pd
import geopandas as gpd
import os
import json

from osi import root_osi_folder
from osi.utils.main import validate_aoi
# convert the modules for image collection (cloudless masking, compositing, reducer etc)
from osi.image_collection.main import ImageCollection
from osi.spectral_indices.spectral_analysis import SpectralAnalysis
from osi.spectral_indices.utils import normalization_100
from osi.hansen.historical_loss import HansenHistorical
from osi.classifying.assign_zone import AssignClassZone
from osi.legends.utils import convert_to_legend_items
from osi.legends.main import LegendsBuilder
from osi.obia.main import OBIASegmentation
from osi.ml.main import LandcoverML
#from osi.arcpy.main import ArcpyOps  # only if using arcgis
from osi.fcd.main_fcd import FCDCalc
from osi.pca.pca_gee import PCA
from osi.hansen.historical_loss import HansenHistorical
from osi.classifying.assign_zone import AssignClassZone
from osi.arcpy.utils import safe_get_data_source



In [3]:
# project gcp
name_project_gcp = 'ee-iwansetiawan'

# setting root_folder, path and variables
#print(root_osi_folder)

#save_dir_output = '/content/drive/Shareddrives/TREEO BD Supply/satellite_verification/2025_notebooks_Satver/20250117_WestNile'
loc_drive_mounted = 'Z:'
save_dir_output = f'{loc_drive_mounted}/Shared drives/TREEO BD Supply/satellite_verification/2025_notebooks_Satver/20250117_WestNile'
input_dir = os.path.join(save_dir_output, '00_input')
output_dir = os.path.join(save_dir_output, '01_output')

os.makedirs(input_dir, exist_ok=True)
os.makedirs(output_dir, exist_ok=True)

########### VARIABLE DEFINITION
is_first_run = True

dict_config = {
    "project_name" : "Oluba_westnile",
    "date_analyzed": '20250117',
    "save_dir_output":save_dir_output,
    "input_dir": os.path.join(save_dir_output, '00_input'),
    "output_dir": os.path.join(save_dir_output, '01_output'),
    "I_satellite":"Planet",
    "pca_scaling":1,
    "tileScale" :1,
    "AOI_path": os.path.join(input_dir, "aoi_extend_oluba.shp"),
    "OID_field_name": "Id",
    #"input_training": f"{loc_drive_mounted}/Shared drives/TREEO BD Supply/02. UGA/01. TPPs/17. Oluba Flagship Conservation Limited/due_diligence/shp/oluba_training_shp.shp",
    "algo_ml_selected": "gbm",
    "date_start_end":["2024-6-1","2024-6-30"],
    "super_pixel_size": 3,

    "region": "africa",

    "pixel_number": 6, #> 0.5 ha
    "year_start_loss": 14, # start 2014  (10 years rule)
    "tree_cover_forest": 10, # > 10 percent

    "band_name_image": "Class",
    "cloud_cover_threshold" : 40,
    "crs_input" : "EPSG:4326",
    "IsThermal": False,

    "fcd_selected": 21,
    "high_forest" : 65,
    "yrf_forest" : 55, # synthetic number
    "shrub_grass" : 35,
    "open_land" : 30,
    "ndwi_hi_sentinel" : 0.05,
    "ndwi_hi_landsat" : 0.1,
    "ndwi_hi_planet" : -0.2,

    "create_training_gee" : True, # if True here then following needs to fill in
    "num_training_to_create": 8, # open, grass, shrub, crop, forest, infra, water, wetland
    }

create_training_gee = dict_config['create_training_gee']
date_analyzed = dict_config['date_analyzed']
# dict_config["location_sample_created"] = f"{loc_drive_mounted}/Shared drives/TREEO BD Supply/02. UGA/01. TPPs/17. Oluba Flagship Conservation Limited/due_diligence/shp/new_oluba_training_{date_analyzed}.shp"
new_sample_gee_created = os.path.join(input_dir , f"new_oluba_training_{date_analyzed}.shp")
dict_config["location_sample_created"] = new_sample_gee_created

# config_json creation - reupdate if any changes happen
config_json_loc = os.path.join(input_dir,f"{dict_config['date_analyzed']}_{dict_config['project_name']}_conf.json")
with open(config_json_loc, 'w') as json_file:
    json.dump(dict_config, json_file, indent=4)

print(f"data created in {config_json_loc}")

data created in Z:/Shared drives/TREEO BD Supply/satellite_verification/2025_notebooks_Satver/20250117_WestNile\00_input\20250117_Oluba_westnile_conf.json


In [4]:
# Trigger the authentication flow. if you want to user json, please comment this
ee.Authenticate()
# Initialize the library
# ee.Initialize(project='bukit30project')
# ee.Initialize(project='treeo-1')
ee.Initialize(project=name_project_gcp)

In [5]:
# using the dict config
config = dict_config
AOIt_shp_plot = geemap.shp_to_ee(config['AOI_path'])
crs_input = config['crs_input']
I_satellite = config['I_satellite']
project_name = config['project_name']

start_date = config['date_start_end'][0]
end_date = config['date_start_end'][1]

layer_name_image_mosaick = f'image_mosaick_result_ee_{project_name}'

AOI = AOIt_shp_plot
config['AOI'] = AOI

ndwi_hi = 0.1
if config['I_satellite'] == 'Landsat':
    ndwi_hi = config['ndwi_hi_landsat']
elif I_satellite == 'Sentinel':
    ndwi_hi = config['ndwi_hi_sentinel']
elif I_satellite == 'Planet':
    ndwi_hi = config['ndwi_hi_planet']

### Masking and overlay and area helper Make an image out of the AOI area attribute -> convert featurecollection into raster (image) for overlaying tools
OID = config['OID_field_name']
AOI_img = AOI.filter(ee.Filter.notNull([OID])).reduceToImage(
    properties= [OID],
    reducer= ee.Reducer.first()
)

In [6]:
if create_training_gee == False:
    # verification format the data input content, training and AOI
    df_training_data = gpd.read_file(config['input_training'])
    print('before_validation: ',df_training_data.shape)
    # Function to check if a value is an integer
    def is_integer(value):
        return isinstance(value, int)
    
    # Filter out non-integer values in the 'code_lu' column
    df_training_data['code_lu'] = df_training_data['code_lu'].apply(lambda x: x if is_integer(x) else None)
    display(df_training_data)
    print('after validation: (if the same, no error found)',df_training_data.shape)

elif create_training_gee == True and is_first_run == False:
    config['input_training'] = new_sample_gee_created
    # verification format the data input content, training and AOI
    df_training_data = gpd.read_file(config['input_training'])
    print('before_validation: ',df_training_data.shape)
    # Function to check if a value is an integer
    def is_integer(value):
        return isinstance(value, int)
    
    # Filter out non-integer values in the 'code_lu' column
    df_training_data['code_lu'] = df_training_data['code_lu'].apply(lambda x: x if is_integer(x) else None)
    display(df_training_data)
    print('after validation: (if the same, no error found)',df_training_data.shape)

# Create a pandas DataFrame from the data AOI
df_AOI = gpd.read_file(config['AOI_path'])
display(df_AOI)

fields = df_AOI.columns.tolist()
print(fields)
#for area id in shapefile that identified the data, and will converted into raster
OID = config['OID_field_name']  #IMPORTANT TO CHECK OID based on the column ID
if OID not in fields:
    print(f'field_name of {OID} is not exist ERROR WILL HAPPEN!!!!')
    raise ValueError(f"Field '{OID}' not found in the fields: {fields}")
else:
    print(f"Field '{OID}' found. Proceeding with operations masking based on AOI \nplease continue")
    # Proceed with further operations, like converting to raster, etc.
    #############################################
    ##################################################################################
    ### Masking and overlay and area helper Make an image out of the AOI area attribute -> convert featurecollection into raster (image) for overlaying tools
    AOI_img = AOI.filter(ee.Filter.notNull([OID])).reduceToImage(
        properties= [OID],
        reducer= ee.Reducer.first()
    )

Id      area_ha  Field                                           geometry
0   0  31451.65138    NaN  POLYGON ((31.34357 3.12811, 31.34462 3.12607, ...

['Id', 'area_ha', 'Field', 'geometry']
Field 'Id' found. Proceeding with operations masking based on AOI 
please continue


In [7]:
# list the class color landcover
pallette_class_segment = {
            '1': '#83ff5a',  # forest_trees (1)
            '2': '#ffe3b3',  # shrubland (2)
            '3': '#ffff33',  # grassland (3)
            '4': '#f89696',  # openland (4)
            '5': '#1900ff',  # waterbody_wet_area (5)
            '6': '#e6e6fa',  # plantation (6)
            '7': '#FFFFFF',   # gray_infrastructure (7)
            '8': '#4B0082',  # oil_palm (8) - Dark Purple
            '9': '#8B4513',  # cropland (9) - Brown
            '10': '#87CEEB',  # waterbody (10) - Light Blue
            '11': '#2F4F4F',  # wetlands (11) - Dark Teal
            '12': '#ADFF2F',  # forest_trees_regrowth (12) - Light Green
            '13': '#8B0000',  # historical_treeloss_10years (13) - Dark Red
            '14': '#DAA520'   # paddy_irrigated (14) - Golden Yellow
            }
if create_training_gee == False:
    unique_training_list = list(df_training_data['code_lu'].unique())
    #list_added_hansen = []  # this should be manually added if we miss [12,13]
    #all_list_displayed = sorted(unique_training_list + list_added_hansen)
    all_list_displayed = unique_training_list

    print(all_list_displayed)
    pallette_class_segment = {str(key): value for key, value in pallette_class_segment.items() if int(key) in all_list_displayed}
    print('updated class list: ', pallette_class_segment)
else:
    all_list_displayed = [k for k,v in pallette_class_segment.items()]

In [8]:
# initialize Map object
Map = geemap.Map(center=(-3, 115), zoom=4)
Map.centerObject(AOI, 10)

In [9]:
# now starting to do analysis add the data to the map for later check
# initiate instance class for the image collection and later mosaicking
classInputCollection = ImageCollection(I_satellite=I_satellite,
                                       AOI=AOI,
                                       date_start_end=config['date_start_end'],
                                       cloud_cover_threshold = config['cloud_cover_threshold'],
                                       region=config['region'])

# run the method from image collection loaded, cloudless compositing until to image_mosaick
image_mosaick = classInputCollection.image_mosaick()

vis_params_image_mosaick = {"bands":["red","green","blue"],"min":0,"max":0.1,"gamma":1}
layer_name_image_mosaick = f'image_mosaick_result_ee_{config["project_name"]}'
# image_mosaick_arcgis_layer = arc_ops.adding_ee_to_arcgisPro(image_mosaick, vis_params_image_mosaick,
#                                                    layer_name_image_mosaick)

if config['I_satellite'] == 'Planet':
    # true color {"bands":["red","green","blue"],"min":0,"max":0.6,"gamma":1.5}
    # nir veg color {"bands":["red","nir","blue"],"min":0,"max":0.6,"gamma":1.5 }
    image_mosaick_layer = Map.addLayer(image_mosaick,{"bands":["red","green","blue"],"min":0,"max":0.6,"gamma":1.5}, f'{I_satellite} mosaicked - {start_date}-{end_date} VegColor')
else:
    image_mosaick_layer = Map.addLayer(image_mosaick,{'bands': ['swir2', 'nir', 'red'], 'min': 0, 'max': 0.6, 'gamma': 1.5 }, f'{I_satellite} mosaicked - {start_date}-{end_date}')



selecting Planet images


In [10]:
Map

Map(center=[3.011694128117981, 31.30620169491727], controls=(WidgetControl(options=['position', 'transparent_b…

In [11]:
classImageSpectral = SpectralAnalysis(image_mosaick,config)
class_FCD_run = FCDCalc(config).fcd_calc()
FCD1_1 = class_FCD_run['FCD1_1']
FCD2_1 = class_FCD_run['FCD2_1']

FCD1_1_layer = Map.addLayer(FCD1_1, {'min':0 ,'max':80, 'palette':['ff4c16', 'ffd96c', '39a71d']},
                                                   f'FCD1_1_{project_name}')

FCD2_1_layer = Map.addLayer(FCD2_1, {'min':0 ,'max':80, 'palette':['ff4c16', 'ffd96c', '39a71d']},
                                                   f'FCD2_1_{project_name}')

print('finish processing PCA please continue')

selecting Planet images
selecting Planet images
processing AVI
processing BSI
processing SI
Normalizing to 100 AVI
Normalizing to 100 AVI
Normalizing to 100 BSI
Normalizing to 100 SI
Combining AVI AND BSI
no thermal band, choosing Planet images
Processing means center of AVI_BSI please wait
Now we proceed to the PCA of Vegetation density
Success get the PCA normalized of VD => SVI
Now calculating the FCD from SVI and SSI - selecting band svi1 svi2 ssi1 and ssi2
finish processing PCA, the result: FCD1_1 and FCD2_1 please continue
finish processing PCA please continue


In [12]:
# Now this is historical data to overlay later with current baseline (landcover)
hansen_class = HansenHistorical(config)
run_hansen = hansen_class.initiate_tcl()
LastImageLandsat, treeLossYear, minLoss, ForestArea2000Hansen, gfc =  \
                                 run_hansen['LastImageLandsat'], \
                                 run_hansen['treeLossYear'], \
                                 run_hansen['minLoss'], \
                                 run_hansen['ForestArea2000Hansen'], \
                                 run_hansen['gfc']

config['AOI_img'] = AOI_img

class_assigning_fcd =  AssignClassZone(config, FCD1_1=FCD1_1, FCD2_1=FCD2_1)
list_images_classified = class_assigning_fcd.assigning_fcd_class(gfc, minLoss)

fcd_classified_zone = list_images_classified['all_zone']

vis_params_fcd_classified = class_assigning_fcd.vis_param_merged
# Convert the dictionary to the LEGEND_ITEMS format
legend_items = convert_to_legend_items(class_assigning_fcd.legend_class)

fcd_classified_zone_layer = Map.addLayer(fcd_classified_zone, vis_params_fcd_classified,
                                                   f'FCD_classified_zone_{project_name}')
print('look at the map, if the visual looks good, please continue, if not, please adjust the synthetic number yrf_forest and high_forest')

########### uncomment if you want to check
# Map.addLayer(treeLossYear.randomVisualizer(), {},
#                                                    f'treeLossYear')

#treeLoss = treeLossYear.gte(0).And(treeLossYear.lte(23)).selfMask()
# Map.addLayer(treeLoss.randomVisualizer(), {},
#                                                    f'treeLoss')

#Canopy cover percentage (e.g. 30%), for Indonesia
#cc = ee.Number(config['tree_cover_forest'])

#Minimum forest area in pixels (e.g. 3 pixels, ~ 0.27 ha in this example).
#pixels = ee.Number(config['pixel_number'])

#Minimum mapping area for tree loss (usually same as the minimum forest area).
#lossPixels = pixels

#canopyCover = gfc.select(['treecover2000'])
#canopyCoverThreshold = canopyCover.gte(cc).selfMask()

#Use connectedPixelCount() to get contiguous area.
#contArea = canopyCoverThreshold.connectedPixelCount()
#Apply the minimum area requirement.
#minArea = contArea.gte(pixels).selfMask()

#treecoverLoss = minArea.And(treeLoss).rename(f'lossfrom_0-23').selfMask()

#Create connectedPixelCount() to get contiguous area.
#contLoss = treecoverLoss.connectedPixelCount()
#Apply the minimum area requirement, and get the TCL data ---> minLoss - ACTUAL TCL AREA from Hansen since the year_start_loss
#minLoss = contLoss.gte(lossPixels).selfMask()


#Map.addLayer(minLoss.randomVisualizer(), {},
#                                                   f'minLoss')
#####################################

Adding the map of Forest, FCD >= 55% and mask only if not water in area (hansen) and NDWI
Adding the map of Shrubland, FCD <  55% and FCD >= 35%
Adding the map of Grassland or Openland, FCD  < 35%
Processing - the zoning classification
finish processing, merging all the zone into one image
look at the map, if the visual looks good, please continue, if not, please adjust the synthetic number yrf_forest and high_forest


In [13]:
image_mosaick_all_bands = image_mosaick.addBands([FCD2_1.select('FCD').rename('FCD2_1'), FCD1_1.select('FCD').rename('FCD1_1')])

## ADDING DIRECTLY SPECTRAL INDICES
# classImageSpectral
pca_scale = classImageSpectral.pca_scale
ndwi_image = classImageSpectral.NDWI_func()
msavi2_image = classImageSpectral.MSAVI2_func()
mtvi2_image = classImageSpectral.MTVI2_func()
ndvi_image = classImageSpectral.NDVI_func()
vari_image = classImageSpectral.VARI_func()

image_mosaick_ndvi_ndwi_msavi2_mtvi2_vari = (
    image_mosaick_all_bands
    .addBands(ndwi_image)
    .addBands(msavi2_image)
    .addBands(mtvi2_image)
    .addBands(ndvi_image)
    .addBands(vari_image)
)

red_norm = normalization_100(image_mosaick.select(['red']), pca_scale=pca_scale, AOI=AOI)
green_norm = normalization_100(image_mosaick.select(['green']), pca_scale=pca_scale, AOI=AOI)
blue_norm = normalization_100(image_mosaick.select(['blue']), pca_scale=pca_scale, AOI=AOI)
nir_norm = normalization_100(image_mosaick.select(['nir']), pca_scale=pca_scale, AOI=AOI)

image_norm = red_norm.addBands(green_norm).addBands(blue_norm).addBands(nir_norm)

image_norm_ndvi = normalization_100(image_mosaick_ndvi_ndwi_msavi2_mtvi2_vari.select('NDVI'), pca_scale=pca_scale, AOI=AOI)
image_norm_ndwi = normalization_100(image_mosaick_ndvi_ndwi_msavi2_mtvi2_vari.select('ndwi'), pca_scale=pca_scale, AOI=AOI)
image_norm_msavi2 = normalization_100(image_mosaick_ndvi_ndwi_msavi2_mtvi2_vari.select('msavi2'), pca_scale=pca_scale, AOI=AOI)
image_norm_mtvi2 = normalization_100(image_mosaick_ndvi_ndwi_msavi2_mtvi2_vari.select('MTVI2'), pca_scale=pca_scale, AOI=AOI)
image_norm_vari = normalization_100(image_mosaick_ndvi_ndwi_msavi2_mtvi2_vari.select('VARI'), pca_scale=pca_scale, AOI=AOI)

# red_norm.bandNames().getInfo()
image_norm_with_spectral_indices = image_norm.addBands(image_norm_ndvi).addBands(image_norm_ndwi).addBands(image_norm_msavi2).addBands(image_norm_mtvi2).addBands(image_norm_vari)
image_norm_with_spectral_indices_FCD = image_norm_with_spectral_indices.addBands(FCD2_1.select('FCD').rename('FCD2_1')).addBands(FCD1_1.select('FCD').rename('FCD1_1'))

In [14]:
# OBIA MACHINE LEARNING APPROACH
obia = OBIASegmentation(config=config, image=image_norm_with_spectral_indices_FCD, pca_scale=pca_scale) #pca_scale basically is spatial resolution e.g planet: 5
clusters = obia.SNIC_cluster()['clusters']
object_properties_image = obia.summarize_cluster(is_include_std = False)
# make sure has all the same type of data in all bands, for exporting purpose
object_properties_image = object_properties_image.clip(AOI).toFloat()

# create samping by gee or without, or using existing
if create_training_gee:
    num_training_to_create = config['num_training_to_create']
else:
    num_training_to_create = len(df_training_data['code_lu'].unique())

lc = LandcoverML(config=config,
                 input_image = image_norm_with_spectral_indices_FCD,
                cluster_properties=object_properties_image,
                 num_class=num_training_to_create, # make sure this one is align with total type landcover stratification, for a sample creation
                pca_scale = pca_scale)

legend_lc = lc.lc_legend_param()
vis_param_lc = legend_lc['vis_param_lc']

legend_lc = legend_lc['legend_class']
# Convert the dictionary to the LEGEND_ITEMS format
legend_items_lc = convert_to_legend_items(legend_lc)

snic list bands: ['red_mean', 'green_mean', 'blue_mean', 'nir_mean', 'ndwi_mean', 'msavi2_mean', 'MTVI2_mean', 'NDVI_mean', 'VARI_mean', 'FCD1_1_mean', 'FCD2_1_mean', 'area', 'clusters_min', 'width', 'height']


In [15]:
###########THIS IS NEEDED IF YOU WANT TO CREATE TRAINING BASED ON GEE METHOD BELOW SAMPLE
import numpy as np

#create stratified random sampling based on K-means classes
# create_training_gee
if create_training_gee:
    print('yes, we"re creating the sample!!')

    ########### SAMPLE NUMBER CREATION BASED ON https://docs.google.com/spreadsheets/d/1J8MEi4IDn6faok6UUn9L64T61yWk0D4q/edit?gid=1919918133#gid=1919918133
#     # example
#     strata_area_based_kmeans = {
#     'Forest': 100,
#     'Shrub': 100,
#     'Grass': 100,
#     'Crop': 100,
#     'Water': 100
#     }

    # try with K-means input
    random_samples_creation = lc.stratified_random_creation()
    df_sample_n = random_samples_creation['df_sample_n']
    stratified_training = random_samples_creation['stratified_training']

    # Export the samples to a SHP file in Google Drive
    export_stratified_point = ee.batch.Export.table.toDrive(
        collection=stratified_training,
        description=os.path.basename(config["location_sample_created"])[:-4],
        folder=os.path.join(f'{config["project_name"]}_samples_kmeans'), # THIS IS IN YOUR - MYDRIVE, NEED TO COPY TO SHAREDRIVE LATER
        fileFormat='SHP'
    )
    
    # Start the export task
    export_stratified_point.start()
    
    # Monitor the task status
    import time
    while export_stratified_point.active():
        print('Export task status:', export_stratified_point.status())
        time.sleep(10)
    
    print(f'Export task completed: Stratified_Random_Samples_{project_name}')

    # Open in gdrive in your computer
    # location_stratified_exported = config['location_sample_created']
    # print(location_stratified_exported) #make sure the location is correct (G: is connected by gdrive desktop!)

    # # arcgis layer object
    # training_points = map.addDataFromPath(location_stratified_exported)
    # # training_points.name = 'change the name here'

    # path_shp_input_training = training_points.dataSource

    print('Do not continue to next process if you"re not yet label the sample you just created! \n =====================================================\n =====================================')

else:
    print('we will use the existing training_points or labelled')
    print(f'location of the training sample is in {config["input_training"]}')

yes
Class 0: 4403.34 Ha
Class 1: 3526.87 Ha
Class 2: 6050.55 Ha
Class 3: 2164.88 Ha
Class 4: 3690.08 Ha
Class 5: 3605.11 Ha
Class 6: 3342.11 Ha
Class 7: 4668.70 Ha
total sample size:  1968.5608214680417
{'0': 275, '1': 220, '2': 378, '3': 135, '4': 230, '5': 225, '6': 209, '7': 292}
Total samples: 1964
Export task status: {'state': 'READY', 'description': 'Stratified_Random_Samples_Oluba_westnile', 'priority': 100, 'creation_timestamp_ms': 1737140360822, 'update_timestamp_ms': 1737140360822, 'start_timestamp_ms': 0, 'task_type': 'EXPORT_FEATURES', 'id': 'FY36IQ7TXZ7UBHPQDZBSU4TL', 'name': 'projects/ee-iwansetiawan/operations/FY36IQ7TXZ7UBHPQDZBSU4TL'}
Export task status: {'state': 'RUNNING', 'description': 'Stratified_Random_Samples_Oluba_westnile', 'priority': 100, 'creation_timestamp_ms': 1737140360822, 'update_timestamp_ms': 1737140370939, 'start_timestamp_ms': 1737140370810, 'task_type': 'EXPORT_FEATURES', 'attempt': 1, 'id': 'FY36IQ7TXZ7UBHPQDZBSU4TL', 'name': 'projects/ee-iwanset

In [30]:
os.path.basename(config["location_sample_created"])

'new_oluba_training_20250117'

In [25]:


print(f'Export task completed: Stratified_Random_Samples_{project_name}')

Export task status: {'state': 'READY', 'description': 'new_oluba_training_20250117.shp', 'priority': 100, 'creation_timestamp_ms': 1737141898302, 'update_timestamp_ms': 1737141898302, 'start_timestamp_ms': 0, 'task_type': 'EXPORT_FEATURES', 'id': 'P7PKQ6QLTXKIEERIXYI6VCFI', 'name': 'projects/ee-iwansetiawan/operations/P7PKQ6QLTXKIEERIXYI6VCFI'}
Export task status: {'state': 'RUNNING', 'description': 'new_oluba_training_20250117.shp', 'priority': 100, 'creation_timestamp_ms': 1737141898302, 'update_timestamp_ms': 1737141902650, 'start_timestamp_ms': 1737141902486, 'task_type': 'EXPORT_FEATURES', 'attempt': 1, 'id': 'P7PKQ6QLTXKIEERIXYI6VCFI', 'name': 'projects/ee-iwansetiawan/operations/P7PKQ6QLTXKIEERIXYI6VCFI'}
Export task completed: Stratified_Random_Samples_Oluba_westnile


Export task status: {'state': 'READY', 'description': 'new_oluba_training_20250117.shp', 'priority': 100, 'creation_timestamp_ms': 1737141327033, 'update_timestamp_ms': 1737141327033, 'start_timestamp_ms': 0, 'task_type': 'EXPORT_FEATURES', 'id': 'J3GHKCVYMMWFYE5EZUYM4BDO', 'name': 'projects/ee-iwansetiawan/operations/J3GHKCVYMMWFYE5EZUYM4BDO'}
Export task status: {'state': 'RUNNING', 'description': 'new_oluba_training_20250117.shp', 'priority': 100, 'creation_timestamp_ms': 1737141327033, 'update_timestamp_ms': 1737141330351, 'start_timestamp_ms': 1737141330132, 'task_type': 'EXPORT_FEATURES', 'attempt': 1, 'id': 'J3GHKCVYMMWFYE5EZUYM4BDO', 'name': 'projects/ee-iwansetiawan/operations/J3GHKCVYMMWFYE5EZUYM4BDO'}
Export task completed: Stratified_Random_Samples_Oluba_westnile


In [ ]:
################################################

In [ ]:
################################################ Just to make sure above condition met (if you already label the training data!)

In [ ]:
# starting to do ML analysis
classifier = lc.run_classifier()

training_points = classifier['training_points']
validation_points = classifier['validation_points']

rf = classifier['classified_image_rf']
svm = classifier['classified_image_svm']
gbm = classifier['classified_image_gbm']
cart = classifier['classified_image_cart']

# fcd lc, 5 classes only, just nice to know
fcd_lc = list_images_classified['fcd_class_lc_image']
fcd_lc_vs = list_images_classified['vis_param_segment_lc']
fcd_lc_arc = Map.addLayer(fcd_lc,fcd_lc_vs, 'fcd-method_lc_result')
rf_arc = Map.addLayer(rf,vis_param_lc,'Random_forest_lc_result')
svm_arc = Map.addLayer(svm,vis_param_lc,'SVM_lc_result')
gbm_arc = Map.addLayer(gbm,vis_param_lc,'GBM_lc_result')
cart_arc = Map.addLayer(cart,vis_param_lc,'CART_lc_result')

# MATRIX CONFUSION
lc.matrix_confusion(fcd_lc,validation_points,'fcd',output_dir)
lc.matrix_confusion(rf, validation_points, 'rf', output_dir)
lc.matrix_confusion(svm, validation_points, 'svm', output_dir)
lc.matrix_confusion(gbm, validation_points, 'gbm', output_dir)
lc.matrix_confusion(cart, validation_points, 'cart', output_dir)

In [ ]:
algo_ml_selected = config['algo_ml_selected']
selected_image_lc = rf
if config['algo_ml_selected'] == 'rf':
    algo_ml_selected = 'rf'
    selected_image_lc = rf
elif config['algo_ml_selected'] == 'svm':
    algo_ml_selected = 'svm'
    selected_image_lc = svm
elif config['algo_ml_selected'] == 'gbm':
    algo_ml_selected = 'gbm'
    selected_image_lc = gbm
elif config['algo_ml_selected'] == 'cart':
    algo_ml_selected = 'cart'
    selected_image_lc = cart
print('algo_ml_selected: ',algo_ml_selected)

In [ ]:
# legend filter
#class_assigning_fcd =  AssignClassZone(config, FCD1_1=FCD1_1, FCD2_1=FCD2_1) # do not uncomment if you're already run above
#list_images_classified = class_assigning_fcd.assigning_fcd_class(gfc, minLoss)

#fcd_classified_zone = list_images_classified['all_zone']

#execute the method to update the vis_params and legend_class
class_assigning_fcd.restrict_zone_from_lc(list_class_lc=all_list_displayed)
legend_items_zone = convert_to_legend_items(class_assigning_fcd.legend_class)
vis_param_ml_classified = class_assigning_fcd.vis_param_merged

# re-overlay the data for zoning from the selected method if they give the best metric, and when we check visually the land cover map make sense, also FCD approach is already there
image_for_zone = selected_image_lc

# comment this first, just check the LC above, then run the overlay zoning classification after
HighForestDense = list_images_classified['HighForestDense']

final_zone = class_assigning_fcd.assign_zone_ml(image_for_zone, minLoss,AOI_img, HighForestDense)
Map.addLayer(final_zone, vis_param_ml_classified, f'Final_zone_ML_{algo_ml_selected}_Hansen_test')  # the naming probably will need to change, for some concistencies only so that you understand again later to read the codes


In [ ]:
#additional data
# Load DEM data (replace 'dataset' with your actual DEM dataset)
DEM = ee.Image('USGS/SRTMGL1_003').clip(AOI)

# Calculate slope in degrees
slope = ee.Terrain.slope(DEM)

# Convert slope to percentage
slopePercentage = slope.expression('tan(b*0.01745) * 100', {'b': slope})

# Define slope classification thresholds
thresholds = [8, 15, 25, 40]  # Adjust these thresholds as needed

# Classify slope into categories using conditional statements
slopeClasses = slopePercentage \
    .lte(thresholds[0]).multiply(1) \
    .add(slopePercentage.gt(thresholds[0]).And(slopePercentage.lte(thresholds[1])).multiply(2)) \
    .add(slopePercentage.gt(thresholds[1]).And(slopePercentage.lte(thresholds[2])).multiply(3)) \
    .add(slopePercentage.gt(thresholds[2]).And(slopePercentage.lte(thresholds[3])).multiply(4)) \
    .add(slopePercentage.gt(thresholds[3]).multiply(5))

# Display the classified slope image
palette = ['lightgreen', 'yellow', 'orange', 'pink', 'red']  # Change green to lightgreen
vis_params = {'min': 1, 'max': 5, 'palette': palette}
Map.addLayer(slopeClasses, vis_params, 'Slope Classes')
#arc_ops.adding_ee_to_arcgisPro(slopeClasses, vis_params, 'Slope Classes')
print('finished adding slope')

import pandas as pd

## SOIL Overlay FAO
FAO_soil = ee.Image("users/muhammadiqbaltreeo/HWSD2_FAO").clip(AOI)
# Get the unique values from the image
unique_values = FAO_soil.reduceRegion(
    reducer=ee.Reducer.frequencyHistogram(),
    geometry=AOI.geometry(),
    scale=30
).getInfo()

unique_values = list(unique_values['b1'].keys())
unique_values = [int(f) for f in unique_values]
print('Unique values:', unique_values)

import random

# Generate random colors for each unique value
def get_random_color():
    return "#{:06x}".format(random.randint(0, 0xFFFFFF))


value_color_map = {value: get_random_color() for value in unique_values}
print('Value-Color Map:', value_color_map)

# Create a color palette based on the unique values and their corresponding colors
palette = [value_color_map[value] for value in unique_values]

# Create a visualization dictionary
visualization = {
    'min': min(unique_values),
    'max': max(unique_values),
    'palette': palette
}

smu_table = ee.FeatureCollection("users/muhammadiqbaltreeo/HWSD2_SMU")

# Get the data as a Python dictionary
filtered_smu_table = smu_table.filter(ee.Filter.inList('HWSD2_SMU_ID', unique_values))

# Get the filtered data as a Python dictionary
filtered_smu_data = filtered_smu_table.getInfo()

# Extract the features from the dictionary
features = filtered_smu_data['features']

# Extract properties from each feature
properties_list = [feature['properties'] for feature in features]

# Convert the list of properties to a pandas DataFrame
df_snum = pd.DataFrame(properties_list)

# Display the DataFrame
# display(df_snum)

# Extract the 'name' and 'snum' columns and convert them to a dictionary
name_snum_dict = df_snum.set_index('HWSD2_SMU_ID')['name'].to_dict()
print(name_snum_dict)

# Update the legend dictionary to use the format "snum: name_soil"
legend_dict = {f"{snum}: {name_snum_dict[snum]}": value_color_map[snum] for snum in unique_values}

# Map.add_legend(title="Soil Type (FAO) Legend", legend_dict=legend_dict)

Map.addLayer(FAO_soil.clip(AOI),visualization,'FAO_soil')
#arc_ops.adding_ee_to_arcgisPro(FAO_soil.clip(AOI),visualization,'FAO_soil')

# Map.addLayer(AOIsmaller.style(**style), {}, 'AOI Smaller')
Map.addLayer(training_points, {'color': 'yellow'},
    'Training data location')
# arc_ops.adding_ee_to_arcgisPro(training_points, {'color': 'yellow'},
#     'Training data location')

Map.addLayer(validation_points, {'color': 'red'},
    'Validation data location')

# arc_ops.adding_ee_to_arcgisPro(validation_points, {'color': 'red'},
#     'Validation data location')


In [ ]:
## legend lc
#legend_class_lc = LegendsBuilder(legend_items=legend_items_lc)
#legend_class_lc.create_legend('landcover')

## legend zone
#legend_class_zone = LegendsBuilder(legend_items=legend_items)
#legend_class_zone.create_legend('final-zone')
#
## custom color spectrum - override example
#legend_class_lc.create_colorbar('Forest Canopy Density',{'min': 0, 'max': 100, 'palette': ['#ff4c16', '#ffd96c', '#39a71d']})

In [ ]:
# testing the restrict params only on available data above - ideally give the same visualization outcomes
legend_lc_restrict = lc.lc_legend_param(list_class_restrict=all_list_displayed)
vis_param_lc_restrict = legend_lc_restrict['vis_param_lc']

legend_lc_restricted_cls = legend_lc_restrict['legend_class']
# Convert the dictionary to the LEGEND_ITEMS format
legend_items_lc_restricted = convert_to_legend_items(legend_lc_restricted_cls)

Map.addLayer(gbm,vis_param_lc_restrict,'GBM_lc_result_restrict_visparams')

In [ ]:
# legend lc
legend_class_lc = LegendsBuilder(legend_items=legend_items_lc_restricted)
legend_class_lc.create_legend('landcover')

# legend zone
legend_class_zone = LegendsBuilder(legend_items=legend_items_zone)
legend_class_zone.create_legend('final-zone')

# custom color spectrum - override example
legend_class_lc.create_colorbar('Forest Canopy Density',{'min': 0, 'max': 100, 'palette': ['#ff4c16', '#ffd96c', '#39a71d']})